<a href="https://colab.research.google.com/github/ravi-0309/Optimisation-Techniques/blob/main/Optimization_using_Genetic_Algorithm.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [214]:
import math
import numpy as np
import random
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from IPython.display import HTML

# Objective Function
def objective(x, dtype = float):
  return 2**(-2*(((x-0.1)**2)/(0.8))**2) * (np.sin(5*np.pi*x))**6

def random_population_generator(population_size, upper_bound, lower_bound):
  return np.random.uniform(lower_bound, upper_bound, population_size)

# Encoded to Decoded Value converter i.e. binary to x
def decode(binary_list, bits):
  boom = []
  for binary in binary_list:
    num = 0
    for j in range(bits):
      k = binary % 10
      binary = binary // 10
      num += (2**j) * k
    decoded_value = lower_bound + actual_error * num
    boom.append(decoded_value)
  return np.array(boom)

# Decoded to Encoded values converter i.e. x to binary
def encode(x_list, bits):
    num_list = [int((x - lower_bound) / actual_error) for x in x_list]
    binaries = []
    for num in num_list:
        binary_str = bin(num)[2:].zfill(bits)
        binaries.append(int(binary_str))
    return np.array(binaries)

# Preserve best values
def elitism(binaries_1, binaries_2):
  elites = []
  total = np.concatenate((binaries_1, binaries_2))
  total = list(set(total))
  total_decoded = decode(total, bits)
  total_fitness = objective(total_decoded)
  sorted = np.argsort(total_fitness)[::-1]
  for i in range(len(binaries_1)):
    elites.append(total[sorted[i]])
  return elites

# Cross-Over
def cross_over(binaries, population_size, bits):
  index = []
  new_binaries = np.zeros(population_size, dtype=int)
  for i in range(int(population_size / 2)):
    index.append(random.randint(0, bits-1))
  for i in range(len(index)):
    new_binaries[2*i] = 10**index[i] * (binaries[2*i] // 10**index[i]) + (binaries[2*i+1] % 10**index[i])
    new_binaries[2*i+1] = 10**index[i] * (binaries[2*i+1] // 10**index[i]) + (binaries[2*i] % 10**index[i])
  return new_binaries

# Mutation
def mutation(binaries, population_size, bits):
    mutated = []
    for binary in binaries:
        binary_str = str(binary).zfill(bits)
        binary_list = list(binary_str)
        point = random.randint(0, bits - 1)
        binary_list[point] = '1' if binary_list[point] == '0' else '0'
        mutated.append(int(''.join(binary_list)))
    return mutated

# Parameters
upper_bound = 1
lower_bound = 0
population_size = 30
error = 0.001
generations = 100

b = ((upper_bound - lower_bound) / error) + 1
bits = math.floor(math.log2(b))
actual_error = ((upper_bound - lower_bound) / (2**bits - 1))
print(f"Number of Bits: {bits}")
print(f"Actual Error: {actual_error}")

initial_x = random_population_generator(population_size, upper_bound, lower_bound)
binaries = encode(initial_x, bits) # Initial Population
decoded_values = decode(binaries, bits)
fitness_values = objective(decoded_values)
sorted = np.argsort(fitness_values)[::-1]
global_best_binaries = [binaries[i] for i in sorted]
global_best_x_values = decode(global_best_binaries, bits)
global_best_fitness = [fitness_values[i] for i in sorted]

best_values_x = np.zeros((generations, population_size))
for i in range(generations):
  print(f"\nGeneration: {i+1}")
  decoded_values = decode(binaries, bits)
  fitness_values = objective(decoded_values)
  global_best_binaries = elitism(global_best_binaries, binaries)
  global_best_values = decode(global_best_binaries, bits)
  print(f"global_best_values: {global_best_values}")
  best_values_x[i] = global_best_values

  # Crossover and Mutation
  binaries = cross_over(global_best_binaries, population_size, bits)
  binaries = mutation(binaries, population_size, bits)

# Create a figure and axis
fig, ax = plt.subplots()
x = np.linspace(lower_bound, upper_bound, int(100 * (upper_bound - lower_bound)))
plt.plot(x, objective(x))
plt.xlabel('x')
plt.ylabel('f(x)')
plt.title('Objective Function')
plt.grid(True)
dots, = ax.plot(best_values_x[0], objective(best_values_x[0]), 'ro')

# Function to update the plot
frame = generations
def update(frame):
  dots.set_data(best_values_x[frame], objective(best_values_x[frame]))
  ax.set_title(f'Generation: {frame + 1}')
  return dots,

# Create animation
ani = FuncAnimation(fig, update, frames=generations, interval=50, blit=True)

# Display animation in Colab
HTML(ani.to_jshtml())

Number of Bits: 9
Actual Error: 0.0019569471624266144

Generation: 1
global_best_values: [0.29158513 0.50880626 0.4853229  0.32093933 0.68493151 0.68297456
 0.47162427 0.0704501  0.90606654 0.46379648 0.06262231 0.33855186
 0.53816047 0.66144814 0.25831703 0.86888454 0.65949119 0.54794521
 0.93542074 0.45009785 0.15264188 0.15655577 0.84148728 0.95499022
 0.77495108 0.57925636 0.01956947 0.97651663 0.20939335 0.19765166]

Generation: 2
global_best_values: [0.29158513 0.30919765 0.50489237 0.50880626 0.31311155 0.4853229
 0.32093933 0.07827789 0.68493151 0.68297456 0.47358121 0.47162427
 0.0704501  0.7260274  0.89236791 0.90606654 0.46575342 0.46379648
 0.06262231 0.26223092 0.33855186 0.53816047 0.26027397 0.66144814
 0.25831703 0.45792564 0.86888454 0.65949119 0.45401174 0.14677104]

Generation: 3
global_best_values: [0.09980431 0.09393346 0.29158513 0.30919765 0.50489237 0.50880626
 0.31311155 0.4853229  0.32093933 0.07827789 0.2778865  0.68493151
 0.68297456 0.32485323 0.47358121 0.